In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import statistics as st

def get_df(day):
    file_name = f"./round-4-island-data-bottle/prices_round_4_day_{day}.csv"
    return pd.read_csv(file_name, sep=';')

def get_product(df, product):
    return df[df['product'] == product].copy()

def get_first_two_dfs():
    first_df = get_df(1)
    second_df = get_df(2)
    second_df['timestamp'] = second_df['timestamp'] + 1000000
    return pd.concat([first_df, second_df])



In [101]:
df = get_first_two_dfs()

In [89]:
df = get_df(1)


In [102]:

df_coconut = get_product(df, 'COCONUT')
df_coconut_call = get_product(df, "COCONUT_COUPON")

In [103]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_coconut['timestamp'], y=df_coconut['mid_price'], name='Coconut Mid Price'))
fig.add_trace(go.Scatter(x=df_coconut_call['timestamp'], y=df_coconut_call['mid_price'], name='Coconut Call Mid Price', yaxis='y2'))
fig.update_layout(title='Coconut and Coconut Call Prices over Timestamp', yaxis=dict(title='Coconut Mid Price'), yaxis2=dict(title='Coconut Call Bid Price', overlaying='y', side='right'))
fig.show()


In [104]:
import numpy as np
norm = st.NormalDist()
# tte in days
def call_price(vol, strike, spot, tte):
    d1 = (np.log(spot) - np.log(strike) + 1/2 vol**2 * tte)/ (vol * np.sqrt(time))
    d2 = d1 - vol * np.sqrt(tte)
    

SyntaxError: invalid syntax. Perhaps you forgot a comma? (2399818362.py, line 5)

In [105]:
import numpy as np
from scipy.stats import norm
from scipy.optimize import brentq

def black_scholes_call(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot / strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    d2 = d1 - volatility * np.sqrt(time_to_expiry)
    call_price = (spot * norm.cdf(d1) - strike * norm.cdf(d2))
    return call_price

def implied_volatility(call_price, spot, strike, time_to_expiry):
    # Define the equation where the root is the implied volatility
    def equation(volatility):
        estimated_price = black_scholes_call(spot, strike, time_to_expiry, volatility)
        return estimated_price - call_price

    # Using Brent's method to find the root of the equation
    implied_vol = brentq(equation, 1e-10, 3.0, xtol=1e-10)
    return implied_vol

# Example usage
spot_price = 10000        # Spot price of the underlying asset
strike_price = 10000      # Strike price of the option
call_price = 637.5         # Market price of the call option
time_to_expiry = 250      # Time to expiry in years
initial_guess = 0.010133165868867465

volatility = implied_volatility(call_price, spot_price, strike_price, time_to_expiry)
print(f"Implied Volatility: {volatility:.8%}")


Implied Volatility: 1.01172617%


In [106]:
df_coconut_call = df_coconut_call.merge(df_coconut[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_coconut'))
df_coconut_call

day  timestamp         product  bid_price_1  bid_volume_1  bid_price_2  \
0        1          0  COCONUT_COUPON        637.0          39.0          NaN   
1        1        100  COCONUT_COUPON        637.0          33.0          NaN   
2        1        200  COCONUT_COUPON        637.0          42.0          NaN   
3        1        300  COCONUT_COUPON        638.0          30.0          NaN   
4        1        400  COCONUT_COUPON        637.0          33.0          NaN   
...    ...        ...             ...          ...           ...          ...   
19995    2    1999500  COCONUT_COUPON        622.0          28.0          NaN   
19996    2    1999600  COCONUT_COUPON        620.0          37.0          NaN   
19997    2    1999700  COCONUT_COUPON        619.0          30.0          NaN   
19998    2    1999800  COCONUT_COUPON        620.0          44.0          NaN   
19999    2    1999900  COCONUT_COUPON        620.0          40.0          NaN   

       bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  \
0               NaN          NaN           NaN          638            39   
1               NaN          NaN           NaN          638            33   
2               NaN          NaN           NaN          638            42   
3               NaN          NaN           NaN          639            30   
4               NaN          NaN           NaN          638            33   
...             ...          ...           ...          ...           ...   
19995           NaN          NaN           NaN          623            43   
19996           NaN          NaN           NaN          621            37   
19997           NaN          NaN           NaN          620            30   
19998           NaN          NaN           NaN          621            44   
19999           NaN          NaN           NaN          621            40   

       ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  \
0              NaN           NaN          NaN           NaN      637.5   
1              NaN           NaN          NaN           NaN      637.5   
2              NaN           NaN          NaN           NaN      637.5   
3              NaN           NaN          NaN           NaN      638.5   
4              NaN           NaN          NaN           NaN      637.5   
...            ...           ...          ...           ...        ...   
19995          NaN           NaN          NaN           NaN      622.5   
19996          NaN           NaN          NaN           NaN      620.5   
19997          NaN           NaN          NaN           NaN      619.5   
19998          NaN           NaN          NaN           NaN      620.5   
19999          NaN           NaN          NaN           NaN      620.5   

       profit_and_loss  mid_price_coconut  
0                  0.0            10000.0  
1                  0.0             9999.5  
2                  0.0             9998.5  
3                  0.0             9999.5  
4                  0.0             9998.5  
...                ...                ...  
19995              0.0             9988.0  
19996              0.0             9987.0  
19997              0.0             9986.5  
19998              0.0             9989.5  
19999              0.0             9990.0  

[20000 rows x 18 columns]

In [107]:
df_coconut_call['vol'] = df_coconut_call.apply(lambda row: implied_volatility(row['mid_price'], row['mid_price_coconut'], strike_price, time_to_expiry), axis=1)

In [110]:
df_coconut_call

day  timestamp         product  bid_price_1  bid_volume_1  bid_price_2  \
0        1          0  COCONUT_COUPON        637.0          39.0          NaN   
1        1        100  COCONUT_COUPON        637.0          33.0          NaN   
2        1        200  COCONUT_COUPON        637.0          42.0          NaN   
3        1        300  COCONUT_COUPON        638.0          30.0          NaN   
4        1        400  COCONUT_COUPON        637.0          33.0          NaN   
...    ...        ...             ...          ...           ...          ...   
19995    2    1999500  COCONUT_COUPON        622.0          28.0          NaN   
19996    2    1999600  COCONUT_COUPON        620.0          37.0          NaN   
19997    2    1999700  COCONUT_COUPON        619.0          30.0          NaN   
19998    2    1999800  COCONUT_COUPON        620.0          44.0          NaN   
19999    2    1999900  COCONUT_COUPON        620.0          40.0          NaN   

       bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  \
0               NaN          NaN           NaN          638            39   
1               NaN          NaN           NaN          638            33   
2               NaN          NaN           NaN          638            42   
3               NaN          NaN           NaN          639            30   
4               NaN          NaN           NaN          638            33   
...             ...          ...           ...          ...           ...   
19995           NaN          NaN           NaN          623            43   
19996           NaN          NaN           NaN          621            37   
19997           NaN          NaN           NaN          620            30   
19998           NaN          NaN           NaN          621            44   
19999           NaN          NaN           NaN          621            40   

       ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  \
0              NaN           NaN          NaN           NaN      637.5   
1              NaN           NaN          NaN           NaN      637.5   
2              NaN           NaN          NaN           NaN      637.5   
3              NaN           NaN          NaN           NaN      638.5   
4              NaN           NaN          NaN           NaN      637.5   
...            ...           ...          ...           ...        ...   
19995          NaN           NaN          NaN           NaN      622.5   
19996          NaN           NaN          NaN           NaN      620.5   
19997          NaN           NaN          NaN           NaN      619.5   
19998          NaN           NaN          NaN           NaN      620.5   
19999          NaN           NaN          NaN           NaN      620.5   

       profit_and_loss  mid_price_coconut       vol  
0                  0.0            10000.0  0.010117  
1                  0.0             9999.5  0.010121  
2                  0.0             9998.5  0.010130  
3                  0.0             9999.5  0.010137  
4                  0.0             9998.5  0.010130  
...                ...                ...       ...  
19995              0.0             9988.0  0.009980  
19996              0.0             9987.0  0.009956  
19997              0.0             9986.5  0.009945  
19998              0.0             9989.5  0.009935  
19999              0.0             9990.0  0.009931  

[20000 rows x 19 columns]

In [108]:
df_coconut_call
import plotly.express as px

fig = px.line(df_coconut_call, x='timestamp', y='vol', title='Implied Volatility over Time')
fig.show()


In [117]:
df_coconut_call

day  timestamp         product  bid_price_1  bid_volume_1  bid_price_2  \
0        1          0  COCONUT_COUPON        637.0          39.0          NaN   
1        1        100  COCONUT_COUPON        637.0          33.0          NaN   
2        1        200  COCONUT_COUPON        637.0          42.0          NaN   
3        1        300  COCONUT_COUPON        638.0          30.0          NaN   
4        1        400  COCONUT_COUPON        637.0          33.0          NaN   
...    ...        ...             ...          ...           ...          ...   
19995    2    1999500  COCONUT_COUPON        622.0          28.0          NaN   
19996    2    1999600  COCONUT_COUPON        620.0          37.0          NaN   
19997    2    1999700  COCONUT_COUPON        619.0          30.0          NaN   
19998    2    1999800  COCONUT_COUPON        620.0          44.0          NaN   
19999    2    1999900  COCONUT_COUPON        620.0          40.0          NaN   

       bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  \
0               NaN          NaN           NaN          638            39   
1               NaN          NaN           NaN          638            33   
2               NaN          NaN           NaN          638            42   
3               NaN          NaN           NaN          639            30   
4               NaN          NaN           NaN          638            33   
...             ...          ...           ...          ...           ...   
19995           NaN          NaN           NaN          623            43   
19996           NaN          NaN           NaN          621            37   
19997           NaN          NaN           NaN          620            30   
19998           NaN          NaN           NaN          621            44   
19999           NaN          NaN           NaN          621            40   

       ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  \
0              NaN           NaN          NaN           NaN      637.5   
1              NaN           NaN          NaN           NaN      637.5   
2              NaN           NaN          NaN           NaN      637.5   
3              NaN           NaN          NaN           NaN      638.5   
4              NaN           NaN          NaN           NaN      637.5   
...            ...           ...          ...           ...        ...   
19995          NaN           NaN          NaN           NaN      622.5   
19996          NaN           NaN          NaN           NaN      620.5   
19997          NaN           NaN          NaN           NaN      619.5   
19998          NaN           NaN          NaN           NaN      620.5   
19999          NaN           NaN          NaN           NaN      620.5   

       profit_and_loss  mid_price_coconut       vol  
0                  0.0            10000.0  0.010117  
1                  0.0             9999.5  0.010121  
2                  0.0             9998.5  0.010130  
3                  0.0             9999.5  0.010137  
4                  0.0             9998.5  0.010130  
...                ...                ...       ...  
19995              0.0             9988.0  0.009980  
19996              0.0             9987.0  0.009956  
19997              0.0             9986.5  0.009945  
19998              0.0             9989.5  0.009935  
19999              0.0             9990.0  0.009931  

[20000 rows x 19 columns]

In [118]:
from plotly.subplots import make_subplots
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Scatter(x=df_coconut_call['timestamp'], y=df_coconut_call['mid_price'], name="Mid Price"), secondary_y=False)
fig.add_trace(go.Scatter(x=df_coconut_call['timestamp'], y=df_coconut_call['mid_price_coconut'], name="Mid Price Coconut"), secondary_y=False)
fig.add_trace(go.Scatter(x=df_coconut_call['timestamp'], y=df_coconut_call['vol'], name="Volatility"), secondary_y=True)

fig.update_layout(title_text="Mid Price, Mid Price Coconut, and Volatility over Time")
fig.update_xaxes(title_text="Time")
fig.update_yaxes(title_text="Price", secondary_y=False)
fig.update_yaxes(title_text="Volatility", secondary_y=True)

fig.show()
